##### Copyright 2020 The TensorFlow Authors.


In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Normalizations

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://www.tensorflow.org/addons/tutorials/layers_normalizations"><img src="https://www.tensorflow.org/images/tf_logo_32px.png" />View on TensorFlow.org</a>
  </td>
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/tensorflow/addons/blob/master/docs/tutorials/layers_normalizations.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/tensorflow/addons/blob/master/docs/tutorials/layers_normalizations.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
  <td>
    <a href="https://storage.googleapis.com/tensorflow_docs/addons/docs/tutorials/layers_normalizations.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png" />Download notebook</a>
  </td>
</table>


## Overview
This notebook gives a brief introduction into the [normalization layers](https://github.com/tensorflow/addons/blob/master/tensorflow_addons/layers/normalizations.py) of TensorFlow. Currently supported layers are:
* **Group Normalization** (TensorFlow Addons)
* **Instance Normalization** (TensorFlow Addons)
* **Layer Normalization** (TensorFlow Core)

The basic idea behind these layers is to normalize the output of an activation layer to improve the convergence during training. In contrast to [batch normalization](https://keras.io/layers/normalization/) these normalizations do not work on batches, instead they normalize the activations of a single sample, making them suitable for recurrent neural networks as well. 

Typically the normalization is performed by calculating the mean and the standard deviation of a subgroup in your input tensor. It is also possible to apply a scale and an offset factor to this as well.


$y_{i} = \frac{\gamma ( x_{i} - \mu )}{\sigma }+ \beta$

$ y$ : Output

$x$ : Input

$\gamma$ : Scale factor

$\mu$: mean

$\sigma$: standard deviation

$\beta$: Offset factor


The following image demonstrates the difference between these techniques. Each subplot shows an input tensor, with N as the batch axis, C as the channel axis, and (H, W)
as the spatial axes (Height and Width of a picture for example). The pixels in blue are normalized by the same mean and variance, computed by aggregating the values of these pixels.

![](https://github.com/shaohua0116/Group-Normalization-Tensorflow/raw/master/figure/gn.png)

Source: (https://arxiv.org/pdf/1803.08494.pdf)

The weights gamma and beta are trainable in all normalization layers to compensate for the possible lost of representational ability. You can activate these factors by setting the `center` or the `scale` flag to `True`. Of course you can use `initializers`, `constraints` and `regularizer` for `beta` and `gamma` to tune these values during the training process. 

## Setup

### Install Tensorflow 2.0 and Tensorflow-Addons

In [2]:
!pip install -U tensorflow-addons

  Using cached tensorflow_addons-0.17.1-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.1 MB)


  Using cached typeguard-2.13.3-py3-none-any.whl (17 kB)


In [3]:
import tensorflow as tf
import tensorflow_addons as tfa

### Preparing Dataset

In [4]:
mnist = tf.keras.datasets.mnist

(x_train, y_train),(x_test, y_test) = mnist.load_data()
x_train, x_test = x_train / 255.0, x_test / 255.0

## Group Normalization Tutorial 

### Introduction
Group Normalization(GN) divides the channels of your inputs into smaller sub groups and normalizes these values based on their mean and variance. Since GN works on a single example this technique is batchsize independent. 

GN experimentally scored closed to batch normalization in image classification tasks. It can be beneficial to use GN instead of Batch Normalization in case your overall batch_size is low, which would lead to bad performance of batch normalization  

###Example
Splitting 10 channels after a Conv2D layer into 5 subgroups in a standard "channels last" setting:

In [5]:
model = tf.keras.models.Sequential([
  # Reshape into "channels last" setup.
  tf.keras.layers.Reshape((28,28,1), input_shape=(28,28)),
  tf.keras.layers.Conv2D(filters=10, kernel_size=(3,3),data_format="channels_last"),
  # Groupnorm Layer
  tfa.layers.GroupNormalization(groups=5, axis=3),
  tf.keras.layers.Flatten(),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dropout(0.2),
  tf.keras.layers.Dense(10, activation='softmax')
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
model.fit(x_test, y_test)

  1/313 [..............................] - ETA: 8:43 - loss: 3.5235 - accuracy: 0.0938

 20/313 [>.............................] - ETA: 0s - loss: 1.4862 - accuracy: 0.5781  

 40/313 [==>...........................] - ETA: 0s - loss: 1.1169 - accuracy: 0.6656

 60/313 [====>.........................] - ETA: 0s - loss: 0.9184 - accuracy: 0.7214

 81/313 [======>.......................] - ETA: 0s - loss: 0.8087 - accuracy: 0.7581

...

244/313 [======================>.......] - ETA: 0s - loss: 0.5256 - accuracy: 0.8402

264/313 [========================>.....] - ETA: 0s - loss: 0.5034 - accuracy: 0.8460

284/313 [==========================>...] - ETA: 0s - loss: 0.4865 - accuracy: 0.8507

304/313 [============================>.] - ETA: 0s - loss: 0.4737 - accuracy: 0.8556

313/313 [==============================] - 2s 3ms/step - loss: 0.4725 - accuracy: 0.8565


## Instance Normalization Tutorial
### Introduction
Instance Normalization is special case of group normalization where the group size is the same size as the channel size (or the axis size).

Experimental results show that instance normalization performs well on style transfer when replacing batch normalization. Recently, instance normalization has also been used as a replacement for batch normalization in GANs.

### Example
Applying InstanceNormalization after a Conv2D Layer and using a uniformed initialized scale and offset factor.

In [6]:
model = tf.keras.models.Sequential([
  # Reshape into "channels last" setup.
  tf.keras.layers.Reshape((28,28,1), input_shape=(28,28)),
  tf.keras.layers.Conv2D(filters=10, kernel_size=(3,3),data_format="channels_last"),
  # LayerNorm Layer
  tfa.layers.InstanceNormalization(axis=3, 
                                   center=True, 
                                   scale=True,
                                   beta_initializer="random_uniform",
                                   gamma_initializer="random_uniform"),
  tf.keras.layers.Flatten(),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dropout(0.2),
  tf.keras.layers.Dense(10, activation='softmax')
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
model.fit(x_test, y_test)

  1/313 [..............................] - ETA: 2:36 - loss: 2.3047 - accuracy: 0.0312

 21/313 [=>............................] - ETA: 0s - loss: 2.0439 - accuracy: 0.3378  

 42/313 [===>..........................] - ETA: 0s - loss: 1.6122 - accuracy: 0.5208

 64/313 [=====>........................] - ETA: 0s - loss: 1.2883 - accuracy: 0.6143

 85/313 [=======>......................] - ETA: 0s - loss: 1.1010 - accuracy: 0.6673

...

232/313 [=====================>........] - ETA: 0s - loss: 0.6595 - accuracy: 0.7996

253/313 [=======================>......] - ETA: 0s - loss: 0.6340 - accuracy: 0.8071

274/313 [=========================>....] - ETA: 0s - loss: 0.6106 - accuracy: 0.8149

295/313 [===========================>..] - ETA: 0s - loss: 0.5898 - accuracy: 0.8203

313/313 [==============================] - 1s 2ms/step - loss: 0.5736 - accuracy: 0.8249


## Layer Normalization Tutorial
### Introduction
Layer Normalization is special case of group normalization where the group size is 1. The mean and standard deviation is calculated from all activations of a single sample.

Experimental results show that Layer normalization is well suited for Recurrent Neural Networks, since it works batchsize independently.

### Example

Applying Layernormalization after a Conv2D Layer and using a scale and offset factor. 

In [7]:
model = tf.keras.models.Sequential([
  # Reshape into "channels last" setup.
  tf.keras.layers.Reshape((28,28,1), input_shape=(28,28)),
  tf.keras.layers.Conv2D(filters=10, kernel_size=(3,3),data_format="channels_last"),
  # LayerNorm Layer
  tf.keras.layers.LayerNormalization(axis=3 , center=True , scale=True),
  tf.keras.layers.Flatten(),
  tf.keras.layers.Dense(128, activation='relu'),
  tf.keras.layers.Dropout(0.2),
  tf.keras.layers.Dense(10, activation='softmax')
])

model.compile(optimizer='adam',
              loss='sparse_categorical_crossentropy',
              metrics=['accuracy'])
model.fit(x_test, y_test)

  1/313 [..............................] - ETA: 2:11 - loss: 2.3820 - accuracy: 0.2500

 15/313 [>.............................] - ETA: 1s - loss: 1.3252 - accuracy: 0.5854  

 30/313 [=>............................] - ETA: 1s - loss: 0.9877 - accuracy: 0.6812

 45/313 [===>..........................] - ETA: 0s - loss: 0.8210 - accuracy: 0.7389

 61/313 [====>.........................] - ETA: 0s - loss: 0.7284 - accuracy: 0.7695

...

264/313 [========================>.....] - ETA: 0s - loss: 0.4239 - accuracy: 0.8705

280/313 [=========================>....] - ETA: 0s - loss: 0.4154 - accuracy: 0.8723

296/313 [===========================>..] - ETA: 0s - loss: 0.4108 - accuracy: 0.8742

312/313 [============================>.] - ETA: 0s - loss: 0.4021 - accuracy: 0.8772

313/313 [==============================] - 1s 3ms/step - loss: 0.4019 - accuracy: 0.8773


## Literature
[Layer norm](https://arxiv.org/pdf/1607.06450.pdf)

[Instance norm](https://arxiv.org/pdf/1607.08022.pdf)

[Group Norm](https://arxiv.org/pdf/1803.08494.pdf)